In [108]:
import time

import numpy as np
import pandas as pd
import selenium
from selenium.webdriver.common.by import By

In [94]:
league_id = '61bfd8d70585467faeaddfd5a3c5dbe6'

In [145]:
browser = selenium.webdriver.Chrome()
browser.get(f"https://app.musicleague.com/home/")
print("Login in the Chromium window, and then return here...")

Login in the Chromium window, and then return here...


#### Crawl the Rounds

In [147]:
browser.get(f"https://app.musicleague.com/l/{league_id}")
time.sleep(3)
el = browser.find_element(By.XPATH, "//h4[text()[contains(.,'Completed Rounds')]]/..")
rounds = []
for sub_el in el.find_elements(By.XPATH, "//div[@class[contains(.,'p-4')]]"):
    round_id = sub_el.get_attribute('id')
    round_name = sub_el.find_element(By.XPATH, ".//h5").text
    rounds.append(dict(round_id=round_id, round_name=round_name))
len(rounds)

16

#### Crawl all the Votes

In [154]:
votes = []
for i, round in enumerate(rounds):
    print(round)
    browser.get(f"https://app.musicleague.com/l/{league_id}/{round['round_id']}")
    time.sleep(3)

    for vote_el in browser.find_elements(By.XPATH, "//div[@id[contains(.,'-voter-')]]"):
        if '\n' not in vote_el.text: continue  # no points, just comment
        voter, points = vote_el.text.split('\n')
        points = int(points)

        parent_text = vote_el.find_element(By.XPATH, "../../..").text
        if 'Missed Voting Deadline' in parent_text: continue
        song, artist, album, _, _, submitter = parent_text.split('\n')[:6]
        submitter = submitter[len("Submitted by "):]
        vote = round.copy()
        vote.update(dict(
            song=song, artist=artist, album=album, submitter=submitter,
            voter=voter, points=points,
        ))
        print(vote)
        votes.append(vote)

{'round_id': '5420055fffb8436aae0d867905b04352', 'round_name': 'Earworms'}
{'round_id': '5420055fffb8436aae0d867905b04352', 'round_name': 'Earworms', 'song': 'Total Eclipse of the Heart', 'artist': 'Bonnie Tyler', 'album': 'The Very Best of Bonnie Tyler', 'submitter': 'someben', 'voter': 'Adam Gimpert', 'points': 3}
{'round_id': '5420055fffb8436aae0d867905b04352', 'round_name': 'Earworms', 'song': 'Total Eclipse of the Heart', 'artist': 'Bonnie Tyler', 'album': 'The Very Best of Bonnie Tyler', 'submitter': 'someben', 'voter': 'Dennis', 'points': 3}
{'round_id': '5420055fffb8436aae0d867905b04352', 'round_name': 'Earworms', 'song': 'Total Eclipse of the Heart', 'artist': 'Bonnie Tyler', 'album': 'The Very Best of Bonnie Tyler', 'submitter': 'someben', 'voter': 'Jenny Scherer Gimpert', 'points': 3}
{'round_id': '5420055fffb8436aae0d867905b04352', 'round_name': 'Earworms', 'song': 'Total Eclipse of the Heart', 'artist': 'Bonnie Tyler', 'album': 'The Very Best of Bonnie Tyler', 'submitter':

In [155]:
vote_df = pd.DataFrame(votes)
vote_df['song_artist'] = [' / '.join(els) for els in zip(vote_df['song'], vote_df['artist'])]
vote_df

round_id round_name  \
0    5420055fffb8436aae0d867905b04352   Earworms   
1    5420055fffb8436aae0d867905b04352   Earworms   
2    5420055fffb8436aae0d867905b04352   Earworms   
3    5420055fffb8436aae0d867905b04352   Earworms   
4    5420055fffb8436aae0d867905b04352   Earworms   
..                                ...        ...   
794  9e08ec6a11494ca8a2196640139b6cf0     Covers   
795  9e08ec6a11494ca8a2196640139b6cf0     Covers   
796  9e08ec6a11494ca8a2196640139b6cf0     Covers   
797  9e08ec6a11494ca8a2196640139b6cf0     Covers   
798  9e08ec6a11494ca8a2196640139b6cf0     Covers   

                                       song  \
0                Total Eclipse of the Heart   
1                Total Eclipse of the Heart   
2                Total Eclipse of the Heart   
3                Total Eclipse of the Heart   
4                Total Eclipse of the Heart   
..                                      ...   
794                           Maniac - Live   
795  Creepin' (with The Weeknd & 21 Savage)   
796  Creepin' (with The Weeknd & 21 Savage)   
797  Creepin' (with The Weeknd & 21 Savage)   
798  Creepin' (with The Weeknd & 21 Savage)   

                                  artist                          album  \
0                           Bonnie Tyler  The Very Best of Bonnie Tyler   
1                           Bonnie Tyler  The Very Best of Bonnie Tyler   
2                           Bonnie Tyler  The Very Best of Bonnie Tyler   
3                           Bonnie Tyler  The Very Best of Bonnie Tyler   
4                           Bonnie Tyler  The Very Best of Bonnie Tyler   
..                                   ...                            ...   
794                       Carpenter Brut              CARPENTERBRUTLIVE   
795  Metro Boomin, The Weeknd, 21 Savage              HEROES & VILLAINS   
796  Metro Boomin, The Weeknd, 21 Savage              HEROES & VILLAINS   
797  Metro Boomin, The Weeknd, 21 Savage              HEROES & VILLAINS   
798  Metro Boomin, The Weeknd, 21 Savage              HEROES & VILLAINS   

          submitter                  voter  points  \
0           someben           Adam Gimpert       3   
1           someben                 Dennis       3   
2           someben  Jenny Scherer Gimpert       3   
3           someben                   Kate       3   
4           someben              Bridgette       2   
..              ...                    ...     ...   
794         someben           Adam Gimpert       1   
795  Luke Skywalker               San Holo       3   
796  Luke Skywalker           Adam Gimpert       1   
797  Luke Skywalker            Alexis Rosa       1   
798  Luke Skywalker                   Kate       1   

                                           song_artist  
0            Total Eclipse of the Heart / Bonnie Tyler  
1            Total Eclipse of the Heart / Bonnie Tyler  
2            Total Eclipse of the Heart / Bonnie Tyler  
3            Total Eclipse of the Heart / Bonnie Tyler  
4            Total Eclipse of the Heart / Bonnie Tyler  
..                                                 ...  
794                     Maniac - Live / Carpenter Brut  
795  Creepin' (with The Weeknd & 21 Savage) / Metro...  
796  Creepin' (with The Weeknd & 21 Savage) / Metro...  
797  Creepin' (with The Weeknd & 21 Savage) / Metro...  
798  Creepin' (with The Weeknd & 21 Savage) / Metro...  

[799 rows x 9 columns]

#### Winner!

In [159]:
total_points_vec = vote_df.groupby('submitter').sum()['points'].sort_values(ascending=False)
total_points_vec

submitter
Kate                     202
San Holo                 194
Adam Gimpert             161
someben                  160
elise                    150
Jenny Scherer Gimpert    125
Alexis Rosa              123
Luke Skywalker           123
Bridgette                 89
Dennis                    82
Name: points, dtype: int64

#### Number of Rounds Played

In [160]:
num_rounds_vec = vote_df.groupby(['round_name', 'submitter']).first().reset_index()[['round_name', 'submitter']].groupby('submitter').size().sort_values(ascending=False)
num_rounds_vec

submitter
Adam Gimpert             16
Kate                     16
San Holo                 16
someben                  16
Alexis Rosa              15
Luke Skywalker           15
elise                    14
Jenny Scherer Gimpert    13
Dennis                   12
Bridgette                11
dtype: int64

#### Points per Round

In [162]:
(total_points_vec / num_rounds_vec).sort_values(ascending=False)

submitter
Kate                     12.625000
San Holo                 12.125000
elise                    10.714286
Adam Gimpert             10.062500
someben                  10.000000
Jenny Scherer Gimpert     9.615385
Alexis Rosa               8.200000
Luke Skywalker            8.200000
Bridgette                 8.090909
Dennis                    6.833333
dtype: float64

In [251]:
vote_df.to_csv('/tmp/gimp_sweet_symph1.csv')

In [236]:
import itertools
players = sorted(list(vote_df['submitter'].unique()))
player_pairs = list(itertools.combinations(players, 2))
round_names = sorted(list(vote_df['round_name'].unique()))
round_name_pairs = list(itertools.combinations(round_names, 2))
round_names

['Covers',
 'Dance',
 'Disney',
 'Duet',
 'Earworms',
 'Female Leads',
 'Guilty Pleasure',
 'Instrumental',
 'Movie Songs',
 'New',
 'Old-school Hiphop',
 'One Hit Wonders',
 'Punk',
 'Second Chances',
 'Showtunes',
 'TV Songs']

In [225]:
vs_vecs = []
corr_vecs = []
for round_id in vote_df['round_id'].unique():
    round_vote_df = vote_df[vote_df['round_id'] == round_id]
    vs_df = pd.pivot_table(round_vote_df, index='voter', columns='submitter', values='points').reindex(players, axis=0).reindex(players, axis=1).fillna(0)
    vs_vec = vs_df.unstack()
    vs_vec.name = round_vote_df['round_name'].iloc[0]
    vs_vecs.append(vs_vec)
    corr_vec = vs_df.corr().unstack()
    corr_vec.name = round_vote_df['round_name'].iloc[0]
    corr_vecs.append(corr_vec)

In [245]:
vs_df = pd.concat(vs_vecs, axis=1)
vs_df.loc[player_pairs].corr().unstack().loc[round_name_pairs].sort_values()

Second Chances  TV Songs            -0.396453
                Showtunes           -0.257580
Instrumental    Showtunes           -0.256329
Covers          Showtunes           -0.185299
Dance           Second Chances      -0.124842
                                       ...   
Earworms        Punk                 0.459140
Disney          New                  0.460661
Covers          Instrumental         0.564468
Duet            Old-school Hiphop    0.575598
                Guilty Pleasure      0.651210
Length: 120, dtype: float64

In [250]:
corr_df = pd.concat(corr_vecs, axis=1)
corr_df.loc[player_pairs].mean(axis=1).sort_values()

submitter              submitter            
Kate                   someben                 -0.235995
Luke Skywalker         elise                   -0.192886
Bridgette              Kate                    -0.162813
Jenny Scherer Gimpert  San Holo                -0.145323
Bridgette              Jenny Scherer Gimpert   -0.133856
                       Dennis                  -0.122127
Dennis                 San Holo                -0.121488
Bridgette              San Holo                -0.118501
                       elise                   -0.117090
Jenny Scherer Gimpert  Luke Skywalker          -0.112722
Adam Gimpert           Dennis                  -0.111857
Alexis Rosa            Jenny Scherer Gimpert   -0.104340
                       someben                 -0.092539
                       San Holo                -0.091004
Jenny Scherer Gimpert  Kate                    -0.087651
Dennis                 Luke Skywalker          -0.081256
elise                  someben             